In [71]:
import os
import sys
import numpy as np
import torch

from datetime import datetime
from typing import Tuple

from torch.nn import Module
import torch.nn.functional as F
from torch.nn import KLDivLoss, CrossEntropyLoss, CosineEmbeddingLoss
from torch.optim import Adam
from torch.optim.lr_scheduler import ReduceLROnPlateau

### Loading Teacher model ---> CLIP Image Extractor 

In [ ]:
import clip

model_name = "ViT-B/32"

# model is the torch model.
# preprocess function is for image preprocessing.

model, preprocess = clip.load(model_name)

# Get only the visual model
teacher_model = model.visual
input_resolution = model.visual.input_resolution

print(
    "Model parameters:",
    f"{np.sum([int(np.prod(p.shape)) for p in model.visual.parameters()]):,}",
)
print("Input resolution:", input_resolution)

### Instantiating Student model 

[VisionTransformer](https://github.com/openai/CLIP/blob/d50d76daa670286dd6cacf3bcd80b5e4823fc8e1/clip/model.py#L206)

In [ ]:
from clip.model import VisionTransformer
from clip.model import convert_weights # Make them float16
# Set Student Configuration

patch_size = 32
width = 384
layers = 6
heads = 12
output_dim = 512

student_model = VisionTransformer(
    input_resolution=input_resolution,
    patch_size=patch_size,
    width=width,
    layers=layers,
    heads=heads,
    output_dim=output_dim,
)



convert_weights(student_model)


print(
    "Model parameters:",
    f"{np.sum([int(np.prod(p.shape)) for p in student_model.parameters()]):,}",
)


### Load the WIT Dataset

In [ ]:
from concurrent.futures import ThreadPoolExecutor
from functools import partial
import io
import urllib

import PIL.Image

from datasets import load_dataset
from datasets.utils.file_utils import get_datasets_user_agent


def fetch_single_image(image_url, timeout=None, retries=0):
    for _ in range(retries + 1):
        try:
            request = urllib.request.Request(
                image_url,
                data=None,
                headers={"user-agent": get_datasets_user_agent()},
            )
            with urllib.request.urlopen(request, timeout=timeout) as req:
                image = PIL.Image.open(io.BytesIO(req.read()))
            break
        except Exception:
            image = None
    return image


def fetch_images(batch, num_threads, timeout=None, retries=0):
    fetch_single_image_with_args = partial(
        fetch_single_image, timeout=timeout, retries=retries
    )
    with ThreadPoolExecutor(max_workers=num_threads) as executor:
        batch["image"] = list(
            executor.map(fetch_single_image_with_args, batch["image_url"])
        )
    return batch


num_threads = 20
dset = load_dataset("cifar10")
# dset = dset.map(
#     fetch_images, batched=True, batch_size=100, fn_kwargs={"num_threads": num_threads}
# )

In [ ]:
import torchvision
import torchvision.transforms as transforms

transform = transforms.Compose([
                transforms.Resize(224),
                transforms.RandomCrop(224),
                #transforms.RandomHorizontalFlip(),
                transforms.ToTensor(),
     transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])

cifar100 = torchvision.datasets.CIFAR100('data/',download=True,train=True,transform=transform)
train_dataloader = torch.utils.data.DataLoader(cifar100,
                                          batch_size=4,
                                          shuffle=True,
                                          num_workers=8)

In [ ]:
class DistillationTrainer:
    def __init__(self, *args, **kwargs):
        self.teacher = teacher_model
        self.student = student_model
        self.preprocess = preprocess
        self.train_dataloader = train_dataloader

        self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        self.teacher = self.teacher.to(self.device)
        self.student = self.student.to(self.device)
        self.teacher.eval()

        self.epochs = 30
        self.start_epoch = 1

        # set up optimizer
        self.optimizer = Adam(self.student.parameters(),lr=0.0001)

        # Set up LR Scheduler
        self.lr_scheduler = ReduceLROnPlateau(self.optimizer, "min")

    def compute_loss(self, images, return_outputs=False):
        images = images.to(self.device).half()
        outputs_student = self.student(images)

        # compute teacher output
        with torch.no_grad():
            outputs_teacher = self.teacher(images)

        # assert size
        assert outputs_student.size() == outputs_teacher.size()

        # Soften probabilities and compute distillation loss
        
        print("Before Loss ")
        print("outputs_student",outputs_student)
        print("outputs_teacher",outputs_teacher)
        # KL Divergence Loss
        loss = 0 
#         kl_loss = KLDivLoss(reduction="batchmean",log_target =True)
#         loss = kl_loss(F.log_softmax(outputs_student),F.log_softmax(outputs_teacher))
        # Cosine loss
        loss = loss + CosineEmbeddingLoss()(
            outputs_teacher, outputs_student, torch.ones(outputs_teacher.size()[0]).to(self.device)
        )

        return  loss

    def train(self):
        for epoch in range(self.start_epoch, self.epochs + 1):
            loss_value = self._train_epoch(epoch)
            print(f"KLD-CosineLoss after {epoch} Epoch is {loss_value}")

    def _train_epoch(self, epoch):
        loss_value = 0
        for batch_idx, (images, _) in enumerate(self.train_dataloader):
            
            loss = self.compute_loss( images)
            print(loss)
            loss_value += loss

            self.optimizer.zero_grad()
            
            loss.backward()
            
            self.optimizer.step()
            
            torch.autograd.set_detect_anomaly(True)
            
            if batch_idx % 10 == 0:
                print(f"Loss after {batch_idx} Batch is {loss_value/(batch_idx+1)} ")

        return loss_value.detach().cpu().numpy() / len(self.train_dataloader)

In [ ]:
Trainer = DistillationTrainer(
    teacher_model=teacher_model,
    student_model=student_model,
    train_dataloader=train_dataloader,
    preprocess = preprocess,
)

In [88]:
Trainer.train()

Before Loss 
outputs_student tensor([[-0.7388, -0.7339, -0.2544,  ...,  0.3210,  0.2468,  0.6230],
        [ 0.0182, -0.6816, -0.0752,  ..., -0.9097, -1.2627,  1.2275],
        [-0.7944, -0.9746,  0.2808,  ..., -0.1247, -0.6689,  1.4512],
        [-0.8433, -1.1465,  0.1843,  ..., -0.5142, -0.7632,  1.4170]],
       device='cuda:0', dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.2181,  0.0105, -0.4763,  ...,  1.1885,  0.0987,  0.0034],
        [-0.1395,  0.1727, -0.2703,  ...,  0.8687, -0.2437, -0.0152],
        [ 0.2505,  0.4880, -0.2688,  ...,  0.7422, -0.0636, -0.0924],
        [-0.0498, -0.2864, -0.3735,  ...,  0.6250,  0.0225,  0.3813]],
       device='cuda:0', dtype=torch.float16)
tensor(1., device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Loss after 0 Batch is 1.0 
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan,

Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.0283, -0.0120, -0.0847,  ...,  0.9233,  0.2600,  0.0150],
        [ 0.2087,  0.1022, -0.4045,  ...,  0.6216,  0.0068,  0.2869],
        [ 0.2484,  0.3079, -0.1107,  ...,  0.8770,  0.1857,  0.0529],
        [ 0.0265,  0.0417, -0.1326,  ...,  0.5859, -0.0679, -0.2708]],
       device='cuda:0', dtype=torch.float16)
tensor(nan, device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tens

Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.2573, -0.2397, -0.1908,  ...,  0.8755, -0.3230, -0.0560],
        [ 0.1700,  0.0986, -0.0720,  ...,  0.3979, -0.2922, -0.1670],
        [-0.0754,  0.2959, -0.2725,  ...,  0.9336,  0.0854,  0.0665],
        [ 0.2778,  0.4514, -0.1006,  ...,  0.7769,  0.1198,  0.2074]],
       device='cuda:0', dtype=torch.float16)
tensor(nan, device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tens

Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.2537,  0.1090, -0.1887,  ...,  1.0518,  0.1171,  0.1809],
        [ 0.3992,  0.3145, -0.5615,  ...,  0.9976,  0.0469, -0.4189],
        [-0.2136, -0.2725, -0.2188,  ...,  0.6831, -0.2729, -0.1305],
        [ 0.3408, -0.3760, -0.0490,  ...,  0.5918,  0.3379,  0.1055]],
       device='cuda:0', dtype=torch.float16)
tensor(nan, device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Loss after 40 Batch is nan 
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBack

Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.3262,  0.2153, -0.2026,  ...,  0.6260, -0.2301, -0.1753],
        [ 0.1909, -0.0145, -0.4438,  ...,  0.6968, -0.2983,  0.3940],
        [ 0.0503, -0.2079, -0.1667,  ...,  0.8462, -0.0712, -0.3184],
        [ 0.0659, -0.0537, -0.4695,  ...,  0.7861, -0.2411,  0.0692]],
       device='cuda:0', dtype=torch.float16)
tensor(nan, device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tens

...

Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.3569,  0.2786, -0.1859,  ...,  1.0439, -0.3696,  0.0157],
        [ 0.2209,  0.3337, -0.5005,  ...,  0.6694, -0.6333, -0.3862],
        [ 0.0858,  0.2333, -0.5952,  ...,  0.5811,  0.0947,  0.1010],
        [ 0.3633, -0.1058, -0.2927,  ...,  0.5547,  0.0036, -0.2321]],
       device='cuda:0', dtype=torch.float16)
tensor(nan, device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tens

Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.1879, -0.1599, -0.4128,  ...,  0.8652, -0.0251,  0.0775],
        [ 0.2949,  0.2102, -0.3420,  ...,  0.9067,  0.0662,  0.0200],
        [ 0.5088,  0.2477, -0.0179,  ...,  0.5796, -0.0648,  0.1818],
        [ 0.1672,  0.5161, -0.2325,  ...,  0.6211, -0.1770, -0.1877]],
       device='cuda:0', dtype=torch.float16)
tensor(nan, device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Loss after 6030 Batch is nan 
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBa

Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tensor([[ 0.0703,  0.0454, -0.2429,  ...,  0.7446, -0.1526, -0.0285],
        [-0.5117,  0.0696, -0.0864,  ...,  0.6260, -0.1949, -0.2064],
        [ 0.2661,  0.3574, -0.0474,  ...,  0.7759, -0.2168, -0.1567],
        [-0.1626, -0.0196, -0.5337,  ...,  1.0176, -0.1074, -0.0839]],
       device='cuda:0', dtype=torch.float16)
tensor(nan, device='cuda:0', dtype=torch.float16, grad_fn=<AddBackward0>)
Before Loss 
outputs_student tensor([[nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan],
        [nan, nan, nan,  ..., nan, nan, nan]], device='cuda:0',
       dtype=torch.float16, grad_fn=<MmBackward0>)
outputs_teacher tens

Exception ignored in: <bound method _MultiProcessingDataLoaderIter.__del__ of <torch.utils.data.dataloader._MultiProcessingDataLoaderIter object at 0x7fec19b7bac8>>
Traceback (most recent call last):
  File "/home/ecbm4040/envTF24/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/home/ecbm4040/envTF24/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 1301, in _shutdown_workers
    w.join(timeout=_utils.MP_STATUS_CHECK_INTERVAL)
  File "/usr/lib/python3.6/multiprocessing/process.py", line 124, in join
    res = self._popen.wait(timeout)
  File "/usr/lib/python3.6/multiprocessing/popen_fork.py", line 47, in wait
    if not wait([self.sentinel], timeout):
  File "/usr/lib/python3.6/multiprocessing/connection.py", line 911, in wait
    ready = selector.select(timeout)
  File "/usr/lib/python3.6/selectors.py", line 376, in select
    fd_event_list = self._poll.poll(timeout)
KeyboardInterrupt: 


KeyboardInterrupt: 

In [ ]:
for x in train_dataloader:
    print(x[0].shape,x[1].shape)
    break

In [ ]:
# torch.save(
#     {
#         "distilbert": student_distil_bert.state_dict(),
#     },
#     f"distiled_distilbert_sst2_{datetime.now():%Y-%m-%d_%H-%M-%S%z}.pt",
# )